In [1]:
!export PROTOCOL_BUFFERS_PYTHON_IMPLEMENTATION=python


In [2]:
from collections import OrderedDict
from tqdm import tqdm
from dataset.cad_dataset import get_dataloader
from config import ConfigAE
from utils import cycle
from trainer import TrainerAE
cfg = ConfigAE('train')
tr_agent = TrainerAE(cfg)

SyntaxError: invalid syntax (trainerAE.py, line 23)

In [25]:
from submodules.chamfer_dist import ChamferDistanceL1,ChamferDistanceL2

cfdL1=ChamferDistanceL1()
cfdL2=ChamferDistanceL2()
import torch
import trimesh
from pytorch3d.io import load_objs_as_meshes
from pytorch3d.ops import sample_points_from_meshes
from pytorch3d.vis.plotly_vis import plot_scene
from pytorch3d.structures import Pointclouds
from pytorch3d.structures import Meshes
mesh_trimesh = trimesh.load("/home/edre/dtw_files/DeepCAD/data/full_data/cad_mesh/0002/00020470.stl")
print(mesh_trimesh)
vertices = torch.tensor(mesh_trimesh.vertices, dtype=torch.float32)
faces = torch.tensor(mesh_trimesh.faces, dtype=torch.int64)

# 创建 PyTorch3D 的 Meshes 对象
mesh_pytorch3d = Meshes(verts=[vertices], faces=[faces])
num_samples = 10000
points = sample_points_from_meshes(mesh_pytorch3d, num_samples)

mesh_trimesh2=trimesh.load('/home/edre/dtw_files/DeepCAD/data/mini_data/cad_mesh/0067/00670634.stl')
vertices2 = torch.tensor(mesh_trimesh2.vertices, dtype=torch.float32)
faces2 = torch.tensor(mesh_trimesh2.faces, dtype=torch.int64)

# 创建 PyTorch3D 的 Meshes 对象
mesh_pytorch3d2 = Meshes(verts=[vertices2], faces=[faces2])
num_samples = 10000
points2 = sample_points_from_meshes(mesh_pytorch3d2, num_samples)

<trimesh.Trimesh(vertices.shape=(30, 3), faces.shape=(60, 3), name=`00020470.stl`)>


In [26]:
points=points.cuda()
points2=points2.cuda()

In [27]:
loss=cfdL1(points,points2)

In [28]:
print(loss)

tensor(0.0967, device='cuda:0')


In [7]:
torch.__version__

'1.13.0+cu117'

In [32]:
pcd=Pointclouds(points2)

In [33]:
plot_scene({
    "pointcloud": {"points": pcd}
})

# 数据清洗
发现mesh有的是空的，清洗一下

In [13]:
import json 
with open('/home/edre/dtw_files/DeepCAD/data/cad_data/train_val_test_split.json','r') as f :
    data=json.load(f)

In [36]:
import os
import trimesh
import json

train_num = 800
test_num = 100

# 创建目标目录的基本结构
os.makedirs('data/full_data/cad_vec', exist_ok=True)
os.makedirs('data/full_data/cad_mesh', exist_ok=True)

def load_and_validate_mesh(path):
    try:
        mesh = trimesh.load(path, force='mesh')
        if mesh.is_empty:
            print(f"Warning: The mesh at {path} is empty.")
            return False
        return True
    except Exception as e:
        print(f"Failed to load mesh at {path}: {str(e)}")
        return False

def create_symlinks_and_collect_paths(file_paths, target_folder, num_samples):
    paths_collected = []
    count = 0
    for path in file_paths:
        h5_data = os.path.join('data/cad_data/cad_vec', path + '.h5')
        mesh_data = os.path.join('data/cad_data/cad_mesh', path + '.stl')
        
        if load_and_validate_mesh(mesh_data) and os.path.exists(h5_data) and os.path.exists(mesh_data):
            # 创建目标路径，保留原始的目录结构
            target_h5_path = os.path.join('data/full_data/cad_vec', path+'.h5')
            target_mesh_path = os.path.join('data/full_data/cad_mesh',path+'.stl' )

            # 创建必要的目录
            os.makedirs(os.path.dirname(target_h5_path), exist_ok=True)
            os.makedirs(os.path.dirname(target_mesh_path), exist_ok=True)

            # 创建符号链接，先检查是否已存在
            if os.path.exists(target_h5_path):
                os.remove(target_h5_path)
            if os.path.exists(target_mesh_path):
                os.remove(target_mesh_path)

            os.symlink(os.path.abspath(h5_data), target_h5_path)
            os.symlink(os.path.abspath(mesh_data), target_mesh_path)
            
            paths_collected.append(path)
            
            count += 1
            # if count == num_samples:
            #     break
    return paths_collected

# 收集路径
train_paths = create_symlinks_and_collect_paths(data['train'], 'train', train_num)
test_paths = create_symlinks_and_collect_paths(data['test'], 'test', test_num)
val_paths = create_symlinks_and_collect_paths(data['validation'], 'test', test_num)

# 写入JSON文件
split_data = {
    'train': train_paths,
    'test': test_paths,
    'validation':val_paths
}

with open('data/full_data/train_test_split.json', 'w') as json_file:
    json.dump(split_data, json_file, indent=4)


Failed to load mesh at data/cad_data/cad_mesh/0086/00866760.stl: string is not a file: data/cad_data/cad_mesh/0086/00866760.stl
Failed to load mesh at data/cad_data/cad_mesh/0022/00222961.stl: string is not a file: data/cad_data/cad_mesh/0022/00222961.stl
Failed to load mesh at data/cad_data/cad_mesh/0083/00837927.stl: string is not a file: data/cad_data/cad_mesh/0083/00837927.stl
Failed to load mesh at data/cad_data/cad_mesh/0070/00704820.stl: string is not a file: data/cad_data/cad_mesh/0070/00704820.stl
Failed to load mesh at data/cad_data/cad_mesh/0087/00870042.stl: string is not a file: data/cad_data/cad_mesh/0087/00870042.stl
Failed to load mesh at data/cad_data/cad_mesh/0070/00703301.stl: string is not a file: data/cad_data/cad_mesh/0070/00703301.stl
Failed to load mesh at data/cad_data/cad_mesh/0081/00817507.stl: string is not a file: data/cad_data/cad_mesh/0081/00817507.stl
Failed to load mesh at data/cad_data/cad_mesh/0033/00333559.stl: string is not a file: data/cad_data/cad